# Imports

In [1]:
%pip install pandas ydata-profiling ipywidgets scikit-learn

  Using cached ydata_profiling-4.16.1-py2.py3-none-any.whl.metadata (22 kB)
  Using cached scikit_learn-1.6.1-cp312-cp312-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (18 kB)
  Using cached scipy-1.15.2-cp312-cp312-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (61 kB)
  Using cached matplotlib-3.10.0-cp312-cp312-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (11 kB)
  Using cached pydantic-2.11.3-py3-none-any.whl.metadata (65 kB)
  Using cached visions-0.8.1-py3-none-any.whl.metadata (11 kB)
  Using cached numpy-2.1.3-cp312-cp312-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (62 kB)
  Using cached htmlmin-0.1.12-py3-none-any.whl
  Using cached phik-0.12.4-cp312-cp312-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (5.6 kB)
  Using cached tqdm-4.67.1-py3-none-any.whl.metadata (57 kB)
  Using cached seaborn-0.13.2-py3-none-any.whl.metadata (5.4 kB)
  Using cached multimethod-1.12-py3-none-any.whl.metadata (9.6 kB)
  Using cached statsmodels

In [ ]:
import pandas as pd
import numpy as np
import  ydata_profiling
from ydata_profiling import ProfileReport
import seaborn as sns
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import MinMaxScaler

In [57]:
estado_aleatorio = 42
np.random.seed(estado_aleatorio)

# Dataset

In [45]:
df = pd.read_csv('datasetFinal.csv')

In [22]:
df.duplicated().sum()

np.int64(307)

# Pré Processamento

Iremos realizar nessa parte o pré processamento do csv obtido através de web scrapping contendo informações relacionadas a músicas.

## Tratamento de dados faltando

Abaixo é possível visualizar as informações gerais do nosso csv. As informações de características das músicas vão desde a coluna 5 até a coluna 21, seno que dessas as colunas 11-14 não apresentam nenhum valor absoluto.

In [46]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 15455 entries, 0 to 15454
Data columns (total 22 columns):
 #   Column                           Non-Null Count  Dtype  
---  ------                           --------------  -----  
 0   id_musica                        15455 non-null  object 
 1   filme                            15455 non-null  object 
 2   titulo_musica                    15454 non-null  object 
 3   artista_principal                14364 non-null  object 
 4   creditos_completos               15454 non-null  object 
 5   submission_offset_low_level      5475 non-null   float64
 6   average_loudness                 5475 non-null   float64
 7   dynamic_complexity               5475 non-null   float64
 8   mfcc_zero_mean                   5475 non-null   float64
 9   submission_offset_rythm          5475 non-null   float64
 10  bpm                              5475 non-null   float64
 11  bpm_first_peak_mean              0 non-null      float64
 12  bpm_first_peak_med

Iremos remover as colunas `bpm_second_peak_mean`, `bpm_first_peak_median`, `bpm_second_peak_median`, `bpm_first_peak_mean` devido ao fato não existe uma linha onde elas possuem informações sobre as músicas.

In [47]:
print(df.isnull().sum().sort_values(ascending=False))

df = df.drop(columns=['bpm_second_peak_mean', 'bpm_first_peak_median', 'bpm_second_peak_median', 'bpm_first_peak_mean'])

bpm_second_peak_mean               15455
bpm_first_peak_median              15455
bpm_second_peak_median             15455
bpm_first_peak_mean                15455
scale                               9983
key                                 9983
bpm                                 9980
dynamic_complexity                  9980
mfcc_zero_mean                      9980
danceability                        9980
submission_offset_tonal             9980
submission_offset_low_level         9980
submission_offset_rythm             9980
average_loudness                    9980
tuning_frequency                    9980
onset_rate                          9980
tuning_equal_tempered_deviation     9980
artista_principal                   1091
creditos_completos                     1
titulo_musica                          1
id_musica                              0
filme                                  0
dtype: int64


Além disso, devido à origem dos dados para montagem do csv, sabemos que todas as linhas que possuem `null` em `bpm` possuem `null` em todas as outras colunas de informações de características das músicas, por isso podemos remover elas sem problemas. 

Além disso também possuímos 3 linhas que não possuem informações em `scale` e `key`. Como são apenas 3 linhas, iremos remover elas.

In [48]:
df = df[df["scale"].notnull()]

df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 5472 entries, 7 to 15446
Data columns (total 18 columns):
 #   Column                           Non-Null Count  Dtype  
---  ------                           --------------  -----  
 0   id_musica                        5472 non-null   object 
 1   filme                            5472 non-null   object 
 2   titulo_musica                    5472 non-null   object 
 3   artista_principal                5164 non-null   object 
 4   creditos_completos               5471 non-null   object 
 5   submission_offset_low_level      5472 non-null   float64
 6   average_loudness                 5472 non-null   float64
 7   dynamic_complexity               5472 non-null   float64
 8   mfcc_zero_mean                   5472 non-null   float64
 9   submission_offset_rythm          5472 non-null   float64
 10  bpm                              5472 non-null   float64
 11  danceability                     5472 non-null   float64
 12  onset_rate              

## Tratamento de colunas object

Iremos nesse momento tratar as colunas cujo valor é object. Dadas as colunas abaixo, sabemos que as únicas colunas relevantes para o nosso problema são as colunas:
- `filme`: coluna alvo do nosso problema;
- `key` e `scale`: colunas que trazem informações sobre as características das músicas.

In [49]:
print(df.select_dtypes(include='object').dtypes)

id_musica             object
filme                 object
titulo_musica         object
artista_principal     object
creditos_completos    object
key                   object
scale                 object
dtype: object


Dessa forma, iremos remover as outras colunas que trazem informações que não serão utilizadas pelo nosso modelo de IA para previsão.

In [50]:
df = df.drop(columns=['titulo_musica', 'artista_principal', 'creditos_completos'])
print(df.duplicated().sum())

df = df.drop(columns=['id_musica'])

print(df.select_dtypes(include='object').dtypes)

0
filme    object
key      object
scale    object
dtype: object


Por fim, podemos ver abaixo a presença de dados duplicados no nosso dataset após a remoção de todas essas colunas. Note na célula passada que antes de removermos `id_musica` não haviam linhas duplicadas, o que significa que não possuímos músicas duplicadas no nosso dataset. Por conta disso, cada uma das linhas duplicadas evidencia uma determinada tendência de um filme em utilizar músicas com características semelhantes. Como esse tipo de informação é importante para o nosso modelo recomendar um filme através das características de uma música, não iremos remover esses dados duplicados.

In [51]:
df.duplicated().sum()

np.int64(307)

## Exploração dos dados

Abaixo é gerada uma análise exploratória dos dados. Através dela é possível visualizar que algumas coisas precisam ser modificadas no dataset, como as colunas com valores constantes e as colunas que apresentam alta correlação.

In [52]:
# Gera o relatório
profile = ProfileReport(df, title="Relatório Exploratório", explorative=True)

# Exibe no notebook
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 14/14 [00:00<00:00, 234.42it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## Tratamento de colunas constantes

In [53]:
df = df.drop(columns=['submission_offset_low_level', 'submission_offset_rythm', 'submission_offset_tonal'])

## Tratamento de colunas altamente correlacionadas

Iremos utilizar a função abaixo para remover as colunas com correlação superior a 0.7 (seja essa correlação positiva ou negativa). Além disso, essa função irá remover primeiramente as colunas que possuírem mais altas correlações que as outras, de forma a remover primeiro colunas que possuem mais informações redundantes.

In [54]:
def remover_colunas_correlacionadas(df, limite=0.7):
    df_num = df.select_dtypes(include=[np.number])
    cor_matrix = df_num.corr()

    # Matriz booleana com True onde correlação é alta (acima de limite ou abaixo de -limite)
    cor_bool = (cor_matrix.abs() > limite) & (cor_matrix.abs() < 1.0)

    # Criar uma lista dos pares com alta correlação
    pares_correlacionados = []
    for col in cor_bool.columns:
        for idx in cor_bool.index:
            if cor_bool.loc[idx, col] and (idx, col) not in pares_correlacionados and (col, idx) not in pares_correlacionados:
                pares_correlacionados.append((idx, col))

    # Contar quantas correlações fortes cada coluna tem
    colunas_remover = set()
    pares_ativos = set(pares_correlacionados)

    while pares_ativos:
        # Atualiza a contagem
        contagem = {}
        for a, b in pares_ativos:
            contagem[a] = contagem.get(a, 0) + 1
            contagem[b] = contagem.get(b, 0) + 1

        # Seleciona a coluna com maior número de correlações fortes
        coluna_mais_corr = max(contagem, key=contagem.get)
        colunas_remover.add(coluna_mais_corr)

        # Remove todos os pares que incluem essa coluna
        pares_ativos = {(a, b) for (a, b) in pares_ativos if coluna_mais_corr not in (a, b)}

    print(f"\nColunas removidas por alta correlação (>|{limite}|):\n{sorted(colunas_remover)}")
    return df.drop(columns=list(colunas_remover))

df = remover_colunas_correlacionadas(df, limite=0.7)


Colunas removidas por alta correlação (>|0.7|):
['dynamic_complexity', 'mfcc_zero_mean']


## Separamento em treinamento e teste

In [59]:
y = df['filme']
x = df.drop(columns=['filme'])

x_train, x_test, y_train, y_test = train_test_split(
    x, y, test_size=0.2, random_state=estado_aleatorio
)

## One-Hot Encoding

In [75]:
# 1. Criar e treinar o OneHotEncoder
encoder = OneHotEncoder(sparse_output=False)
encoder.fit(x_train[['key', 'scale']])

# 2. Transformar as colunas nos conjuntos de treino e teste
key_scale_train_encoded = encoder.transform(x_train[['key', 'scale']])
key_scale_test_encoded = encoder.transform(x_test[['key', 'scale']])

# 3. Criar nomes para as novas colunas
feature_names = []
for i, cats in enumerate(encoder.categories_):
    col = 'key' if i == 0 else 'scale'
    for cat in cats:
        feature_names.append(f"{col}_{cat}")

# 4. Criar DataFrames com as variáveis codificadas
encoded_train_df = pd.DataFrame(key_scale_train_encoded, columns=feature_names, index=x_train.index)
encoded_test_df = pd.DataFrame(key_scale_test_encoded, columns=feature_names, index=x_test.index)

# 5. Remover as colunas originais e concatenar as novas colunas
x_train = x_train.drop(['key', 'scale'], axis=1)
x_test = x_test.drop(['key', 'scale'], axis=1)

# 6. Concatenar os DataFrames (originais sem 'key' e 'scale' + dados codificados)
x_train = pd.concat([x_train, encoded_train_df], axis=1)
x_test = pd.concat([x_test, encoded_test_df], axis=1)

## Normalização 

In [77]:
scaler = MinMaxScaler()

x_train = scaler.fit_transform(x_train)
x_test = scaler.fit_transform(x_test)